In [11]:
import numpy as np

import gym

from keras.models import Model
from keras.layers import Input, Dense, Dropout
from keras import backend as K
from keras.optimizers import Adam

import numba as nb
from tensorboardX import SummaryWriter

In [158]:
from gym import error, spaces

class Env(object):
    def __init__(self):
        self.reward_range = (-np.inf, np.inf)
        self.action_space = spaces.Box(low=0., high=1., shape=(1,))
        self.observation_space = spaces.Box(low=0., high=1., shape=(1,))

    def step(self, action):
        self.step_num += 1
        done = False
        self.actions.append(action)
        
        previous_obs = self.observation.copy()
        
        reward = 0.001/(abs(self.observation[0] - action[0]) + 0.001)
        print("R:", reward)
        
        #if abs(self.observation[0] - action[0]) < 0.005
        #    reward = 1.
        #else:
        #    reward = 0.
            
        #self.observation[0] = np.random.rand()

        if self.step_num > 10:
            done = True
        
        return self.observation, reward, done, {}

    def reset(self):
        self.step_num = 0
        self.observation = np.array([0.01])
        self.actions = []
        return self.observation

    def render(self, mode='human', close=False):
        print(np.mean(self.actions))
    
    def close(self):
        pass

    def seed(self, seed=None):
        pass

    def configure(self, *args, **kwargs):
        raise NotImplementedError()

    def __del__(self):
        self.close()

    def __str__(self):
        return '<{} instance>'.format(type(self).__name__)

In [159]:
EPISODES = 1000000

LOSS_CLIPPING = 0.2 # Only implemented clipping for the surrogate loss, paper said it was best
EPOCHS = 10
NOISE = 0.001

GAMMA = 0.99

BATCH_SIZE = 256
NUM_ACTIONS = 1
NUM_STATE = 1
HIDDEN_SIZE = 256
ENTROPY_LOSS = 5 * 1e-3 # Does not converge without entropy penalty
LR = 1e-5 # Lower lr stabilises training greatly

DUMMY_ACTION, DUMMY_VALUE = np.zeros((1, NUM_ACTIONS)), np.zeros((1, 1))

def proximal_policy_optimization_loss_continuous(advantage, old_prediction):
    def loss(y_true, y_pred):
        var = K.square(NOISE)
        pi = 3.1415926
        denom = K.sqrt(2 * pi * var)
        prob_num = K.exp(- K.square(y_true - y_pred)/ (2 * var))
        old_prob_num = K.exp(- K.square(y_true - old_prediction)/ (2 * var))

        prob = prob_num/denom
        old_prob = old_prob_num/denom
        r = prob/(old_prob + 1e-10)

        return -K.mean(K.minimum(r * advantage, K.clip(r, min_value=1 - LOSS_CLIPPING, max_value=1 + LOSS_CLIPPING) * advantage))
    return loss


class Agent:
    def __init__(self):
        self.critic = self.build_critic()
        self.actor = self.build_actor_continuous()

        self.env = Env()
        print(self.env.action_space, 'action_space', self.env.observation_space, 'observation_space')
        self.episode = 0
        self.observation = self.env.reset()
        self.reward = []
        self.reward_over_time = []
        self.writer = SummaryWriter('AllRuns/continuous')
        self.gradient_steps = 0

    def build_actor_continuous(self):
        state_input = Input(shape=(NUM_STATE,))
        advantage = Input(shape=(1,))
        old_prediction = Input(shape=(NUM_ACTIONS,))

        x = Dense(HIDDEN_SIZE, activation='relu')(state_input)
        x = Dropout(0.5)(x)
        x = Dense(HIDDEN_SIZE, activation='relu')(x)
        x = Dropout(0.5)(x)

        out_actions = Dense(NUM_ACTIONS, name='output')(x)

        model = Model(inputs=[state_input, advantage, old_prediction], outputs=[out_actions])
        model.compile(optimizer=Adam(lr=LR),
                      loss=[proximal_policy_optimization_loss_continuous(
                          advantage=advantage,
                          old_prediction=old_prediction)])
        model.summary()

        return model

    def build_critic(self):

        state_input = Input(shape=(NUM_STATE,))
        x = Dense(HIDDEN_SIZE, activation='relu')(state_input)
        x = Dropout(0.5)(x)
        x = Dense(HIDDEN_SIZE, activation='relu')(x)
        x = Dropout(0.5)(x)

        out_value = Dense(1)(x)

        model = Model(inputs=[state_input], outputs=[out_value])
        model.compile(optimizer=Adam(lr=LR), loss='mse')

        return model

    def reset_env(self):
        self.episode += 1
        self.observation = self.env.reset()
        self.reward = []

    def get_action_continuous(self):
        p = self.actor.predict([self.observation.reshape(1, NUM_STATE), DUMMY_VALUE, DUMMY_ACTION])
        action = action_matrix = p[0] + np.random.normal(loc=0, scale=NOISE, size=p[0].shape)
        return action, action_matrix, p

    def transform_reward(self):
        if self.episode % 100 == 0:
            print('Episode #', self.episode, '\tfinished with reward', np.array(self.reward).sum(),
                  '\tAverage reward of last 100 episode :', np.mean(self.reward_over_time[-100:]))
        self.reward_over_time.append(np.array(self.reward).sum())
        self.writer.add_scalar('Episode reward', np.array(self.reward).sum(), self.episode)
        for j in range(len(self.reward) - 2, -1, -1):
            self.reward[j] += self.reward[j + 1] * GAMMA

    def get_batch(self):
        batch = [[], [], [], []]

        tmp_batch = [[], [], []]
        while len(batch[0]) < BATCH_SIZE:
            action, action_matrix, predicted_action = self.get_action_continuous()
            observation, reward, done, info = self.env.step(action)
            self.reward.append(reward)

            tmp_batch[0].append(self.observation)
            tmp_batch[1].append(action_matrix)
            tmp_batch[2].append(predicted_action)
            self.observation = observation

            if done:
                self.transform_reward()
                for i in range(len(tmp_batch[0])):
                    obs, action, pred = tmp_batch[0][i], tmp_batch[1][i], tmp_batch[2][i]
                    r = self.reward[i]
                    batch[0].append(obs)
                    batch[1].append(action)
                    batch[2].append(pred)
                    batch[3].append(r)
                tmp_batch = [[], [], []]
                self.env.render()
                self.reset_env()

        obs, action, pred, reward = np.array(batch[0]), np.array(batch[1]), np.array(batch[2]), np.reshape(np.array(batch[3]), (len(batch[3]), 1))
        pred = np.reshape(pred, (pred.shape[0], pred.shape[2]))
        return obs, action, pred, reward

    def run(self):
        while self.episode < EPISODES:
            obs, action, pred, reward = self.get_batch()
            old_prediction = pred
            pred_values = self.critic.predict(obs)

            advantage = reward - pred_values

            actor_loss = []
            critic_loss = []
            for e in range(EPOCHS):
                actor_loss.append(self.actor.train_on_batch([obs, advantage, old_prediction], [action]))
                critic_loss.append(self.critic.train_on_batch([obs], [reward]))
            self.writer.add_scalar('Actor loss', np.mean(actor_loss), self.gradient_steps)
            self.writer.add_scalar('Critic loss', np.mean(critic_loss), self.gradient_steps)

            self.gradient_steps += 1

In [ ]:
ag = Agent()
ag.run()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_202 (InputLayer)       (None, 1)                 0         
_________________________________________________________________
dense_254 (Dense)            (None, 256)               512       
_________________________________________________________________
dropout_203 (Dropout)        (None, 256)               0         
_________________________________________________________________
dense_255 (Dense)            (None, 256)               65792     
_________________________________________________________________
dropout_204 (Dropout)        (None, 256)               0         
_________________________________________________________________
output (Dense)               (None, 1)                 257       
Total params: 66,561
Trainable params: 66,561
Non-trainable params: 0
_________________________________________________________________
WARN: 

/home/nathan/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nathan/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


R: 0.09690779941456829
R: 0.09238987534952132
R: 0.09740647442083585
R: 0.08671550862003528
R: 0.0924825464968609
R: 0.09724782591554845
R: 0.08272585960467849
R: 0.09514173902284027
0.00025183848038480084
R: 0.08636206648362978
R: 0.07806441836611838
R: 0.10106573240010558
R: 0.09350730653009214
R: 0.0806753523557791
R: 0.09471113591798035
R: 0.08327760859817686
R: 0.0772410824814829
R: 0.09726770968625527
R: 0.08620671049835711
R: 0.08500406219042653
-0.0005028503863497728
R: 0.08304729106555558
R: 0.08280100806970568
R: 0.0869615952510219
R: 0.07805957575878279
R: 0.094753777651647
R: 0.08905221173345318
R: 0.09058807041970149
R: 0.08006064004442029
R: 0.09689678685880822
R: 0.07709017276246688
R: 0.10387407368568018
-0.000514564487284981
R: 0.08108834125560957
R: 0.07678657574241012
R: 0.08946567663669236
R: 0.0948083204864261
R: 0.0926118002239434
R: 0.09490595974639907
R: 0.09533702203514141
R: 0.08261611320149026
R: 0.080124348712195
R: 0.0905106483340763
R: 0.0888948117042674
-

R: 0.08268508671448017
0.0003421869013941976
R: 0.10494186059728212
R: 0.08344620190039917
R: 0.0961684069779877
R: 0.09762781650408485
R: 0.10520048878709552
R: 0.10438600662278327
R: 0.10036332991724489
R: 0.09049586178531399
R: 0.10025968442603268
R: 0.10240632344675457
R: 0.08895506850512913
0.0007059519484666068
R: 0.10721558885987222
R: 0.09012447931677874
R: 0.09283450147528509
R: 0.08009792099581722
R: 0.1050514333434606
R: 0.08657048077102283
R: 0.08486620519028198
R: 0.10698138231080162
R: 0.08505802797022927
R: 0.09701899298921662
R: 0.08746027308970555
0.00014744116033961675
R: 0.09273576682421757
R: 0.09512790639475446
R: 0.09376141308774469
R: 0.0895866883554963
R: 0.08016046133047579
R: 0.08626241509588546
R: 0.09928823003668624
R: 0.10176257145403633
R: 0.09667513040678719
R: 0.10049238759481904
R: 0.10921949618654495
0.0004054524135418035
R: 0.08645970841814112
R: 0.09740522160976871
R: 0.10961293545870615
R: 0.09523500949201187
R: 0.08320052463910152
R: 0.099225690180

R: 0.09869767860354554
R: 0.09260748557726284
R: 0.10286129980461399
R: 0.10121127201950307
R: 0.09449549202784649
R: 0.09532677570599503
R: 0.11265849706330376
R: 0.08391415024385565
R: 0.10893431556062855
R: 0.0978049622139809
0.0008512176876026647
R: 0.09979095132849132
R: 0.10771383665248797
R: 0.0982039500852667
R: 0.08774504282730582
R: 0.09198544555113539
R: 0.07907158246318757
R: 0.11018277028559398
R: 0.09830368546905334
R: 0.10183068627395535
R: 0.10136400365235054
R: 0.1002345535807658
0.000698813591335922
R: 0.09117056335148793
R: 0.10944255636749897
R: 0.1053492724583525
R: 0.09696139960741867
R: 0.08637317805919986
R: 0.09546386054686268
R: 0.10316002488845005
R: 0.10056629041640681
R: 0.09563083598483291
R: 0.09216759306865566
R: 0.11399159274134958
0.000847205254829627
R: 0.09301063596160873
R: 0.09911720791928995
R: 0.11032414940880707
R: 0.0918358069985305
R: 0.09052383690170158
R: 0.09708074146835084
R: 0.10505783668961528
R: 0.08823554601377855
R: 0.1040246693227364

...

R: 0.3470001702082624
R: 0.8083315646412795
R: 0.27397140380395335
R: 0.5433706062991731
R: 0.4921466575122762
R: 0.8376245661595642
R: 0.9904535536457727
R: 0.5413633286808691
0.009880923091819946
R: 0.7396739327244198
R: 0.284087842862708
R: 0.5397996724393822
R: 0.47628017576090603
R: 0.8235796949443325
R: 0.41472122555759294
R: 0.8279513859703878
R: 0.6037127107580836
R: 0.9407354084651006
R: 0.4939200326620772
R: 0.6468877424270096
0.01035043865369467
R: 0.6585772594030969
R: 0.6932202395625746
R: 0.7475150026981532
R: 0.5971884907454904
R: 0.37475733571329467
R: 0.7887987169124803
R: 0.3605917847529841
R: 0.38342865145823
R: 0.3898283184801588
R: 0.7302645569798729
R: 0.518788218134844
0.009887776431340655
R: 0.6838391762086047
R: 0.8461987331167754
R: 0.49308115519265544
R: 0.7530442619241114
R: 0.3965457713940492
R: 0.87970699159708
R: 0.6854405488202957
R: 0.31298351742536207
R: 0.5865345030982821
R: 0.4400921945457626
R: 0.801255388057438
0.009643587616207563
R: 0.68366219191

R: 0.48164901335374743
R: 0.49480580593615126
R: 0.5250084175434682
R: 0.41330830763961607
R: 0.4802204207779075
R: 0.832530452145476
0.010151243211262038
R: 0.7230199544356869
R: 0.5884480631757438
R: 0.7573243932749985
R: 0.5115100598420006
R: 0.31819023006869196
R: 0.49886571737247465
R: 0.5156208997442587
R: 0.7215374093246726
R: 0.762627562222541
R: 0.903746808162217
R: 0.6364663298415071
0.009606063282558473
R: 0.9944479010779216
R: 0.571297887915103
R: 0.5977451182495995
R: 0.32286337084895683
R: 0.2343783753948425
R: 0.3154362979515798
R: 0.43742103475092187
R: 0.515527149907669
R: 0.891093296954529
R: 0.3802213839040986
R: 0.8508046942391773
0.009664726200897757
R: 0.8197914048488885
R: 0.7358362709181185
R: 0.5069178178901673
R: 0.6090617280790166
R: 0.4786974268468108
R: 0.6760971830922023
R: 0.497796114862236
R: 0.4897502742006418
R: 0.7063937277045811
R: 0.6834447804403719
R: 0.5413115395757113
0.009804253883905855
R: 0.8062013840446058
R: 0.5927686910588982
R: 0.524301725

R: 0.31091568241929085
R: 0.33323554892546
R: 0.4806284449551906
R: 0.6036082629101687
R: 0.6426874530195762
R: 0.5618429518617625
R: 0.3718531874491331
R: 0.7033753554209293
R: 0.5630167970376433
R: 0.8586389522045063
R: 0.4356831522661489
0.009364548001368522
R: 0.7998493694168494
R: 0.8176427402627547
R: 0.8645401884333842
R: 0.5416453355076378
R: 0.6224419791000131
R: 0.7679425806735611
R: 0.8401798546735404
R: 0.9443832651234023
R: 0.9559845067474292
R: 0.5969528972685824
R: 0.4256714927248164
0.009918072880716354
R: 0.7167339926313717
R: 0.7761852388371274
R: 0.9340400164278448
R: 0.5536690568720332
R: 0.6326629399212385
R: 0.6027512545845496
R: 0.4600482760829746
R: 0.415103128812566
R: 0.6106236721647466
R: 0.5012861427433749
R: 0.3237975986960621
0.009668813322313155
R: 0.5295018258971
R: 0.3264227369206591
R: 0.7537618286763704
R: 0.7548369348510229
R: 0.6658218910662806
R: 0.8770069766408454
R: 0.5228773865209679
R: 0.45594012505045334
R: 0.8976200153677714
R: 0.940633104581

R: 0.6596871956229486
R: 0.4831166943839185
R: 0.6236129924735672
R: 0.4972823804294207
R: 0.6386765006910492
R: 0.8897056424622689
R: 0.7450659821083007
R: 0.8249446756577656
R: 0.5292601709446599
0.010175649679753072
R: 0.3086856350374619
R: 0.5895533473485746
R: 0.5217176475432191
R: 0.5399520125490715
R: 0.44383868210658967
R: 0.7505393124548427
R: 0.47245087917856776
R: 0.48938723569457093
R: 0.8515475137641969
R: 0.6863450387290343
R: 0.8447879193377705
0.009933196764606895
R: 0.46750328670033814
R: 0.5220470314113395
R: 0.5159804311127659
R: 0.5581928838545287
R: 0.35222424809301534
R: 0.6068021318831287
R: 0.9022766128379759
R: 0.8781211970512721
R: 0.7407521061093528
R: 0.30715112756988994
R: 0.6455563730136166
Episode # 13200 	finished with reward 6.496607429637224 	Average reward of last 100 episode : 6.794526378972426
0.009956648538230322
R: 0.9592299677492431
R: 0.4790403319014058
R: 0.7461936040868631
R: 0.9903581164489405
R: 0.5543712994545081
R: 0.6379656733794331
R: 0.

R: 0.9146641938229876
R: 0.6693150538300277
R: 0.41444445515162914
R: 0.44861589496331633
0.010321692700182463
R: 0.3959297924201909
R: 0.558406200875237
R: 0.38037160940471804
R: 0.6542224463128239
R: 0.43600458656859714
R: 0.35850956202496015
R: 0.5514956062349654
R: 0.466701834000653
R: 0.871259881033202
R: 0.4008840858679549
R: 0.35585083787976285
0.009565068475974443
R: 0.3653331683498059
R: 0.6546099567721178
R: 0.2861021327532104
R: 0.4778005070027579
R: 0.5320207596742212
R: 0.34692075660650895
R: 0.491070250177496
R: 0.3484861181541342
R: 0.40139024607404095
R: 0.770911670963589
R: 0.25976376454686617
0.009500695188302719
R: 0.48415465618393805
R: 0.8791350157398363
R: 0.5802581998133767
R: 0.794521299430254
R: 0.4462269232969289
R: 0.5160015332025255
R: 0.4896686821452287
R: 0.7463450208498315
R: 0.46117019550141664
R: 0.7023248559641256
R: 0.9813048475976881
0.010451279357960743
R: 0.593856633663808
R: 0.369101174685579
R: 0.445012365135684
R: 0.5672617744819665
R: 0.9756982

In [57]:
np.mean([0.23, 0.25, 0.1])

0.19333333333333333